# Capstone Project - Cafe location
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a cafe. Specifically, this report will be targeted to stakeholders interested in opening a **coffee place** in **Kiev**, Ukraine.

Since there are lots of cafes in Kiev we will try to detect **locations that are not already crowded with cafes**. We are also particularly interested in **areas with no cafes in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use my data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence my decission are:
* number of existing cafes in the neighborhood (any type of cafe)
* number of and distance to cafes in the neighborhood, if any
* distance of neighborhood from city center

I decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of cafes and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Kiev center will be obtained using geocoder **Nominatum** of well known Kiev location (Khreshchatyk Street)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Kiev city center.

Let's first find the latitude & longitude of Kiev city center, using specific, well known address and geocoder Nominatum.

In [11]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes ssss
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Fetching package metadata .............
Solving package specifications: .

# All requested packages already installed.
# packages in environment at /opt/conda/envs/DSX-Python35:
#
folium                    0.5.0                      py_0    conda-forge
Libraries imported.


In [12]:
address = 'Khreshchatyk, Kiev, Ukraine'

from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
kiev_center = [latitude, longitude]
print('Coordinate of {}: {}'.format(address, kiev_center))

Coordinate of Khreshchatyk, Kiev, Ukraine: [50.4478094, 30.5287584]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Khreshchatyk. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [13]:
!pip install shapely
!pip install pyproj

Requirement not upgraded as not directly required: shapely in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages
Requirement not upgraded as not directly required: pyproj in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages


In [14]:
import shapely.geometry

import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=36, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=36, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Kiev center longitude={}, latitude={}'.format(kiev_center[1], kiev_center[0]))
x, y = lonlat_to_xy(kiev_center[1], kiev_center[0])
print('Kiev center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Kiev center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Kiev center longitude=30.5287584, latitude=50.4478094
Kiev center UTM X=324554.0920229856, Y=5591340.281641376
Kiev center longitude=30.5287584, latitude=50.4478094


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [15]:
kiev_center_x, kiev_center_y = lonlat_to_xy(kiev_center[1], kiev_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = kiev_center_x - 6000
x_step = 600
y_min = kiev_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(kiev_center_x, kiev_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [16]:
!pip install folium

import folium

Requirement not upgraded as not directly required: folium in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages
Requirement not upgraded as not directly required: branca in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from folium)
Requirement not upgraded as not directly required: jinja2 in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from folium)
Requirement not upgraded as not directly required: requests in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from folium)
Requirement not upgraded as not directly required: six in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from folium)
Requirement not upgraded as not directly required: MarkupSafe>=0.23 in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from jinja2->folium)
Requirement not upgraded as not directly required: chardet<3.1.0,>=3.0.2 in /opt/conda/envs/DSX-Python35/lib/python3.5/site-packages (from requests->folium)
Requirement not upgraded as not directly require

In [17]:
map_kiev = folium.Map(location=kiev_center, zoom_start=13)
folium.Marker(kiev_center, popup='Khreshchatyk').add_to(map_kiev)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_kiev)
    #folium.Marker([lat, lon]).add_to(map_kiev)
map_kiev

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Khreshchatyk. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [18]:
addr = location.address
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(kiev_center[0], kiev_center[1], addr))

Reverse geocoding check
-----------------------
Address of [50.4478094, 30.5287584] is: Хрещатик, 6, Героїв Небесної Сотні алея, Черепанова гора, Печерськ, Печерський район, Київ, 1001, Україна


In [19]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = geolocator.geocode([lat, lon]).address
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Україна', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [20]:
addresses[150:170]

['10, Русанівська набережна, Русанівка, Дніпровський район, Київ, 02147',
 'Школа №136, Ентузіастів вулиця, Русанівка, Дніпровський район, Київ, 02147',
 'Русанівка, Дніпровський район, Київ, 020154',
 '32а, Залізнична вулиця, Чоколівка, Солом’янський район, Київ, 03056',
 'Церква Сергія Радонезького, 14, Уманська вулиця, Чоколівка, Солом’янський район, Київ, 03087',
 '19, Юліуса Фучика вулиця, Солом’янка, Солом’янський район, Київ, 03043',
 'Бюро перепусток, Повітрофлотський проспект, Солом’янка, Солом’янський район, Київ, 03049',
 'Київ-Пасажирський, Східний підземний перехід, Кучмин Яр, Солом’янський район, Київ, 03031',
 'Тіп-топ сервіс, 27, Симона Петлюри вулиця, Кудрявець, Київ, Шевченківський район, Київ, 01000-06999',
 'ТТС - 1, 10/18, Льва Толстого вулиця, Го́род Володимира, Київ, Шевченківський район, Київ, 01000-06999',
 'Володимирська вулиця, Го́род Володимира, Київ, Шевченківський район, Київ, 01046',
 'Хрещатик вулиця, Го́род Володимира, Київ, Шевченківський район, Київ, 

Looking good. Let's now place all this into a Pandas dataframe.

In [21]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address  Distance from center  \
0  3, Васильківська вулиця, Голосіїв, Голосіївськ...           5992.495307   
1  4а, Владислава Заремби провулок, Добрий Шлях, ...           5840.376700   
2  2а, Листопадна вулиця, Добрий Шлях, Голосіївсь...           5747.173218   
3  Продукти, 29, Науки проспект, Добрий Шлях, Гол...           5715.767665   
4  42, Столєтова вулиця, Багринова гора, Голосіїв...           5747.173218   
5  Потерна №7, Багринова гора, Голосіївський райо...           5840.376700   
6  Столичне шосе, Китаїв, Голосіївський район, Ки...           5992.495307   
7  33а, Краматорська вулиця, Ширма, Голосіївський...           5855.766389   
8  20, Криворізька вулиця, Ширма, Голосіївський р...           5604.462508   
9  Дитсадок № 41  Веселка, Деміївська вулиця, Дем...           5408.326913   

    Latitude  Longitude              X             Y  
0  50.395913  30.506130  322754.092023  5.585625e+06  
1  50.396094  30.514563  323354.092023  5.585625e+06  
2  50.396274  30.522997  323954.092023  5.585625e+06  
3  50.396453  30.531431  324554.092023  5.585625e+06  
4  50.396632  30.539865  325154.092023  5.585625e+06  
5  50.396810  30.548299  325754.092023  5.585625e+06  
6  50.396988  30.556733  326354.092023  5.585625e+06  
7  50.400310  30.493233  321854.092023  5.586144e+06  
8  50.400491  30.501668  322454.092023  5.586144e+06  
9  50.400672  30.510102  323054.092023  5.586144e+06

...and let's now save/persist this data into local file.

In [22]:
df_locations.to_pickle('./locations.pkl')

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on cafes in each neighborhood.

We're interested in venues in 'food' category, but only those that are places for coffee - coffee shops, cafes, bakeries etc. So we will include in out list only venues that have 'cafe' in category name, and we'll make sure to detect and include all the subcategories of specific 'coffee' category, as we need info on places for coffee in the neighborhood.

Foursquare credentials are defined in the hidden cell bellow.

In [23]:
# @hidden_cell
client_id = 'QBC2GGWN5342MYOCQRKLTTJBKLPIMJYF5CDGQWDALZ1DNPSQ' # your Foursquare ID
client_secret = '3XZIE33VJY0V4KSAWVP0OKOOOLGM4H41SF4JH44W2N0FKIHR' # your Foursquare Secret
version = '20180605' # Foursquare API version

In [24]:
# Category IDs corresponding to coffee places were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

coffee_place_categories = ['4bf58dd8d48988d1e0931735','4bf58dd8d48988d16a941735', '4bf58dd8d48988d1dc931735', '4bf58dd8d48988d179941735', '4bf58dd8d48988d143941735',
                          '4bf58dd8d48988d16d941735', '4bf58dd8d48988d1d0941735'
                  ]

def is_cafe(categories, specific_filter=None):
    cafe_words = ['coffee', 'breakfast', 'lunch', 'bakery', 'tea']
    cafe = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in cafe_words:
            if r in category_name:
                cafe = True
        if 'fast food' in category_name:
            cafe = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            cafe = True
    return cafe, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Deutschland', '')
    address = address.replace(', Germany', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [33]:
# Let's now go over our neighborhood locations and get nearby cafes; we'll also maintain a dictionary of all found cafes and all found coffee places
import pickle

def get_cafes(lats, lons):
    cafes = {}
    cofee_cafes = {}
    location_cafes = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any cafe (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_cafes = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_caf, is_coffee = is_cafe(venue_categories, specific_filter=coffee_place_categories)
            if is_caf:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                cafe = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_coffee, x, y)
                if venue_distance<=300:
                    area_cafes.append(cafe)
                cafes[venue_id] = cafe
                if is_coffee:
                    coffee_places[venue_id] = cafe
        location_cafes.append(area_cafes)
        print(' .', end='')
    print(' done.')
    return cafes, coffee_places, location_cafes

# Try to load from local file system in case we did this before
cafes = {}
coffee_places = {}
location_cafes = []
loaded = False
try:
    with open('cafes_350.pkl', 'rb') as f:
        cafes = pickle.load(f)
    with open('coffee_places_350.pkl', 'rb') as f:
        coffee_places = pickle.load(f)
    with open('location_cafes_350.pkl', 'rb') as f:
        location_places = pickle.load(f)
    print('Cafe data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    cafes, coffee_places, location_cafes = get_cafes(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('cafes_350.pkl', 'wb') as f:
        pickle.dump(cafes, f)
    with open('coffee_places_350.pkl', 'wb') as f:
        pickle.dump(coffee_places, f)
    with open('location_cafes_350.pkl', 'wb') as f:
        pickle.dump(location_cafes, f)
        

In [37]:
import numpy as np

print('Total number of cafes:', len(cafes))
print('Total number of Coffee cafes:', len(coffee_places))
print('Percentage of Coffee cafes: {:.2f}%'.format(len(coffee_places) / len(cafes) * 100))
print('Average number of cafes in neighborhood:', np.array([len(r) for r in location_cafes]).mean())

Total number of cafes: 367
Total number of Coffee cafes: 471
Percentage of Coffee cafes: 128.34%
Average number of cafes in neighborhood: 0.862637362637


In [38]:
print('List of all cafes')
print('-----------------------')
for r in list(cafes.values())[:10]:
    print(r)
print('...')
print('Total:', len(cafes))

List of all cafes
-----------------------
('4ed4a6ec0e61888eaa9e8ca0', 'Кирпичи', 50.44547570839354, 30.49755184162027, 'Київ, Україна', 222, True, 322330.10244847415, 5591155.020238038)
('4d3738c0d8caa1cdd1d474d6', 'Апельсин', 50.4007520154464, 30.528423382089542, 'просп. Науки, 11а, Київ, Україна', 107, True, 324356.2567896106, 5586109.547034207)
('515abdabe4b0c2a1d2dbfcda', 'Espresso bar', 50.44580384909129, 30.515635027251246, 'вул. Богдана Хмельницького, 16-22, Київ, 01030, Україна', 195, True, 323615.04848372366, 5591148.400213591)
('58daa3276ad5a14f534bed26', 'Лігумінка', 50.446179524508764, 30.49605331531024, 'бул. Тараса Шевченка, 33, Київ, Україна', 249, True, 322226.3603810518, 5591236.8514089035)
('5b525d224420d8002c533847', 'DeJavu', 50.427808, 30.57014, 'Київ, Україна', 292, True, 327418.90101980214, 5589019.708985573)
('559bac8f498effd9368131f6', 'Львiвськi пляцки', 50.445434223251624, 30.517094382463892, 'вул. Богдана Хмельницького, 10, Київ, 01001, Україна', 244, True,

In [39]:
print('List of Coffee cafes')
print('---------------------------')
for r in list(coffee_places.values())[:10]:
    print(r)
print('...')
print('Total:', len(coffee_places.values()))

List of Coffee cafes
---------------------------
('4ed4a6ec0e61888eaa9e8ca0', 'Кирпичи', 50.44547570839354, 30.49755184162027, 'Київ, Україна', 222, True, 322330.10244847415, 5591155.020238038)
('579251f1498e1f75f812859d', 'Кав\'ярня "На Розі"', 50.428715, 30.465548, "Povitroflots'kyi prospekt, 34/1, Київ, Україна", 122, True, 319994.5733391108, 5589368.736743989)
('4f8e56877b0c69f4f909d67d', 'Pelle', 50.482312780934436, 30.499398708343506, 'вул. Електриків, 10, Київ, Україна', 290, True, 322599.1434597852, 5595245.909690219)
('4d3738c0d8caa1cdd1d474d6', 'Апельсин', 50.4007520154464, 30.528423382089542, 'просп. Науки, 11а, Київ, Україна', 107, True, 324356.2567896106, 5586109.547034207)
('515abdabe4b0c2a1d2dbfcda', 'Espresso bar', 50.44580384909129, 30.515635027251246, 'вул. Богдана Хмельницького, 16-22, Київ, 01030, Україна', 195, True, 323615.04848372366, 5591148.400213591)
('558edd78498e642c85bb5590', 'Coffee Cup', 50.49959105054552, 30.499676446030367, 'Україна', 130, True, 322683.

In [40]:
print('Cafes around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_cafes[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Cafes around location {}: {}'.format(i+1, names))

Cafes around location
---------------------------
Cafes around location 101: 
Cafes around location 102: Pies & Friends Bakery
Cafes around location 103: Кафе на автомойке
Cafes around location 104: Хлібний, Palais Royal Café
Cafes around location 105: Кафе в Будинку футболу
Cafes around location 106: 
Cafes around location 107: Львівські круасани (Львівські Круасани), Волконский Хлебная Лавка
Cafes around location 108: Кафе "Аркада"/"Arkada" Cafe
Cafes around location 109: Лаврська Харчевня
Cafes around location 110: DeJavu


Let's now see all the collected cafes in our area of interest on map, and let's also show coffee places in different color.

In [41]:
map_Kiev = folium.Map(location=kiev_center, zoom_start=13)
folium.Marker(kiev_center, popup='Khreshchatyk').add_to(map_kiev)
for caf in cafes.values():
    lat = caf[2]; lon = caf[3]
    is_coffee = caf[6]
    color = 'red' if is_coffee else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_kiev)
map_kiev

Looking good. So now we have all the cafes in area within few kilometers from Khreshchatyk, and we know which ones are coffee places! We also know which cafes exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new coffee place!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Kiev that have low cafe density, particularly those with low number of coffee places. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every cafe within 6km from Kiev center** (Khreschatyk). We have also **identified coffee places** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**cafe density**' across different areas of Kiev - we will use **heatmaps** to identify a few promising areas close to center with low number of cafes in general (*and* no coffee places in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two cafes in radius of 250 meters**, and we want locations **without coffee places in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of cafes in every area candidate**:

In [42]:
location_cafes_count = [len(caf) for caf in location_cafes]

df_locations['Cafes in area'] = location_cafes_count

print('Average number of cafes in every area with radius=300m:', np.array(location_cafes_count).mean())

df_locations.head(10)

Average number of cafes in every area with radius=300m: 0.862637362637


Address  Distance from center  \
0  3, Васильківська вулиця, Голосіїв, Голосіївськ...           5992.495307   
1  4а, Владислава Заремби провулок, Добрий Шлях, ...           5840.376700   
2  2а, Листопадна вулиця, Добрий Шлях, Голосіївсь...           5747.173218   
3  Продукти, 29, Науки проспект, Добрий Шлях, Гол...           5715.767665   
4  42, Столєтова вулиця, Багринова гора, Голосіїв...           5747.173218   
5  Потерна №7, Багринова гора, Голосіївський райо...           5840.376700   
6  Столичне шосе, Китаїв, Голосіївський район, Ки...           5992.495307   
7  33а, Краматорська вулиця, Ширма, Голосіївський...           5855.766389   
8  20, Криворізька вулиця, Ширма, Голосіївський р...           5604.462508   
9  Дитсадок № 41  Веселка, Деміївська вулиця, Дем...           5408.326913   

    Latitude  Longitude              X             Y  Cafes in area  
0  50.395913  30.506130  322754.092023  5.585625e+06              0  
1  50.396094  30.514563  323354.092023  5.585625e+06              1  
2  50.396274  30.522997  323954.092023  5.585625e+06              0  
3  50.396453  30.531431  324554.092023  5.585625e+06              2  
4  50.396632  30.539865  325154.092023  5.585625e+06              0  
5  50.396810  30.548299  325754.092023  5.585625e+06              0  
6  50.396988  30.556733  326354.092023  5.585625e+06              0  
7  50.400310  30.493233  321854.092023  5.586144e+06              0  
8  50.400491  30.501668  322454.092023  5.586144e+06              0  
9  50.400672  30.510102  323054.092023  5.586144e+06              2

OK, now let's calculate the **distance to nearest coffee place from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [43]:
distances_to_coffee_place = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for caf in coffee_places.values():
        caf_x = caf[7]
        caf_y = caf[8]
        d = calc_xy_distance(area_x, area_y, caf_x, caf_y)
        if d<min_distance:
            min_distance = d
    distances_to_coffee_place.append(min_distance)

df_locations['Distance to Coffee place'] = distances_to_coffee_place

In [44]:
df_locations.head(10)

Address  Distance from center  \
0  3, Васильківська вулиця, Голосіїв, Голосіївськ...           5992.495307   
1  4а, Владислава Заремби провулок, Добрий Шлях, ...           5840.376700   
2  2а, Листопадна вулиця, Добрий Шлях, Голосіївсь...           5747.173218   
3  Продукти, 29, Науки проспект, Добрий Шлях, Гол...           5715.767665   
4  42, Столєтова вулиця, Багринова гора, Голосіїв...           5747.173218   
5  Потерна №7, Багринова гора, Голосіївський райо...           5840.376700   
6  Столичне шосе, Китаїв, Голосіївський район, Ки...           5992.495307   
7  33а, Краматорська вулиця, Ширма, Голосіївський...           5855.766389   
8  20, Криворізька вулиця, Ширма, Голосіївський р...           5604.462508   
9  Дитсадок № 41  Веселка, Деміївська вулиця, Дем...           5408.326913   

    Latitude  Longitude              X             Y  Cafes in area  \
0  50.395913  30.506130  322754.092023  5.585625e+06              0   
1  50.396094  30.514563  323354.092023  5.585625e+06              1   
2  50.396274  30.522997  323954.092023  5.585625e+06              0   
3  50.396453  30.531431  324554.092023  5.585625e+06              2   
4  50.396632  30.539865  325154.092023  5.585625e+06              0   
5  50.396810  30.548299  325754.092023  5.585625e+06              0   
6  50.396988  30.556733  326354.092023  5.585625e+06              0   
7  50.400310  30.493233  321854.092023  5.586144e+06              0   
8  50.400491  30.501668  322454.092023  5.586144e+06              0   
9  50.400672  30.510102  323054.092023  5.586144e+06              2   

   Distance to Coffee place  
0                314.419713  
1                169.475284  
2                320.988410  
3                192.484785  
4                579.817052  
5                571.964491  
6                526.291076  
7               1072.507771  
8                687.530407  
9                153.030850

In [45]:
print('Average distance to closest coffee place from each area center:', df_locations['Distance to Coffee place'].mean())

Average distance to closest coffee place from each area center: 390.08381856608696


OK, so **on average coffee place can be found within ~390m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of cafes** and try to extract some meaningfull info from that. Also, let's show **borders of Kiev boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from Khreschatyk.

In [46]:
kiev_boroughs_url = 'https://raw.githubusercontent.com/denysboiko/kyivmap/1ad68c16c2aa1f2bfe5a31fbbc261b722fbf6a0c/static/media/kyiv.34272c8c.geojson'
kiev_boroughs = requests.get(kiev_boroughs_url).json()

def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [47]:
cafe_latlons = [[caf[2], caf[3]] for caf in cafes.values()]

coffee_latlons = [[caf[2], caf[3]] for caf in coffee_places.values()]

In [48]:
from folium import plugins
from folium.plugins import HeatMap

map_kiev = folium.Map(location=kiev_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_kiev) #cartodbpositron cartodbdark_matter
HeatMap(cafe_latlons).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
folium.Circle(kiev_center, radius=1000, fill=False, color='white').add_to(map_kiev)
folium.Circle(kiev_center, radius=2000, fill=False, color='white').add_to(map_kiev)
folium.Circle(kiev_center, radius=3000, fill=False, color='white').add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Looks like a few pockets of low cafe density closest to city center can be found **south, south-east and east from Khreschatyk**. 

Let's create another heatmap map showing **heatmap/density of Coffee places** only.

In [49]:
map_kiev = folium.Map(location=kiev_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_kiev) #cartodbpositron cartodbdark_matter
HeatMap(coffee_latlons).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
folium.Circle(kiev_center, radius=1000, fill=False, color='white').add_to(map_kiev)
folium.Circle(kiev_center, radius=2000, fill=False, color='white').add_to(map_kiev)
folium.Circle(kiev_center, radius=3000, fill=False, color='white').add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

This map is not so 'hot' but it also indicates higher density of existing Coffe places directly north and west from Khreschatyk, with closest pockets of **low Coffee place density positioned east, south-east and south from city center**.

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from KIev center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in borough **Pechersk** (another potentially interesting borough is **Podilsky** with large low cafe density north-west from city center, however this borough is less interesting to stakeholders as it's mostly residental and less popular with tourists).

### Pechersk

Analysis of popular travel guides and web sites often mention Pechersk as beautifull, historical, rich with culture, prestigious Kiev neighborhood popular with tourists and loved by Kiev citizens.

*"Pecherskyi District (Ukrainian: Печерський район) is an urban district of Kiev, the capital of Ukraine. It line within the eponymous historical neighborhood, while also including some other historical areas. The Pechersk (Ukrainian: Печерськ, Pechers'k) neighborhood is located on the hills adjoining the right bank of the Dnieper River. The two geographic entities are often confused together. The Pecherskyi District can be considered as the very heart of Ukraine."*

*"Many other historical and architectural monuments are situated here. Here is located Askold's Grave which was depicted by Taras Shevchenko on his painting of 1846. Around the burial was created the Askold Grave Park and was built a wooden church that later was reconstructed into the brick one designed by Andriy Ivanovych Melensky. The church's name is the Saint Nicolas the Miracle-worker Church or Rotonda. There are large residential, industrial, healthcare and military areas in the district, as well as a few picturesque parks and sports venues like the Lobanovsky Dynamo Stadium. Many administrative and educational facilities are situated in the district.
The famous Art nouveau House with Chimaeras and gigantic statue of Mother Motherland are also located in the Pecherskyi District (Lypky and Zvirynets respectively).*

*After the declaration of Ukrainian independence in 1991, the Pecherskyi District retained and developed its role also becoming a luxury residential area. The few large industrial companies located in the district are considering to move elsewhere, pocketing a significant profit from the real estate they hold from the times of the Soviet Ukraine."*(wikipedia.org)

*"Ancient city of Kiev with its numerous interesting sights, varied historic monuments, makes for a fantastic holiday destination"* (kievkyivukraine.com)

Popular with tourists, relatively close to city center and well connected, that borough appear to justify further analysis.

Let's define new, more narrow region of interest, which will include low-cafe-count parts of Pecherskyi District closest to Khreshchatyk.

In [50]:
roi_x_min = kiev_center_x - 2000
roi_y_max = kiev_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_kiev = folium.Map(location=roi_center, zoom_start=14)
HeatMap(cafe_latlons).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Not bad - this nicely covers all the pockets of low cafe density in Pechersk closest to Kiev center.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [51]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of cafes in vicinity** (we'll use radius of **250 meters**) and **distance to closest Coffee place**.

In [52]:
def count_cafes_nearby(x, y, cafes, radius=250):    
    count = 0
    for caf in cafes.values():
        caf_x = caf[7]; caf_y = caf[8]
        d = calc_xy_distance(x, y, caf_x, caf_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_cafe(x, y, cafes):
    d_min = 100000
    for caf in cafes.values():
        caf_x = caf[7]; caf_y = caf[8]
        d = calc_xy_distance(x, y, caf_x, caf_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_cafe_counts = []
roi_coffee_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_cafes_nearby(x, y, cafes, radius=250)
    roi_cafe_counts.append(count)
    distance = find_nearest_cafe(x, y, coffee_places)
    roi_coffee_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [53]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Cafes nearby':roi_cafe_counts,
                                 'Distance to Coffee place':roi_coffee_distances})

df_roi_locations.head(10)

Cafes nearby  Distance to Coffee place   Latitude  Longitude  \
0             1                160.657207  50.412004  30.536957   
1             0                260.039489  50.412033  30.538363   
2             0                396.143180  50.412618  30.529183   
3             0                297.891284  50.412647  30.530589   
4             1                201.367860  50.412677  30.531995   
5             1                111.170197  50.412707  30.533401   
6             1                 64.564778  50.412737  30.534807   
7             1                126.405729  50.412767  30.536214   
8             1                218.605138  50.412797  30.537620   
9             1                248.568311  50.412826  30.539026   

               X             Y  
0  325004.092023  5.587340e+06  
1  325104.092023  5.587340e+06  
2  324454.092023  5.587427e+06  
3  324554.092023  5.587427e+06  
4  324654.092023  5.587427e+06  
5  324754.092023  5.587427e+06  
6  324854.092023  5.587427e+06  
7  324954.092023  5.587427e+06  
8  325054.092023  5.587427e+06  
9  325154.092023  5.587427e+06

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two cafes in radius of 250 meters**, and **no Coffee places in radius of 400 meters**.

In [54]:
good_caf_count = np.array((df_roi_locations['Cafes nearby']<=2))
print('Locations with no more than two cafes nearby:', good_caf_count.sum())

good_cof_distance = np.array(df_roi_locations['Distance to Coffee place']>=400)
print('Locations with no Coffee places within 400m:', good_cof_distance.sum())

good_locations = np.logical_and(good_caf_count, good_cof_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two cafes nearby: 1701
Locations with no Coffee places within 400m: 369
Locations with both conditions met: 369


Let's see how this looks on a map.

In [55]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_kiev = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_kiev)
HeatMap(cafe_latlons).add_to(map_kiev)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev) 
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Looking good. We now have a bunch of locations fairly close to Khreschatyk(mostly in Pechersk and west corner of Dnipropetrovsk district), and we know that each of those locations has no more than two cafes in radius of 250m, and no Coffee place closer than 400m. Any of those locations is a potential candidate for a new Coffee place, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [56]:
map_kiev = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Looking good. What we have now is a clear indication of zones with low number of cafes in vicinity, and *no* Coffee places at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [57]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_kiev = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_kiev)
HeatMap(cafe_latlons).add_to(map_kiev)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_kiev)
folium.Marker(kiev_center).add_to(map_kiev)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_kiev) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [58]:
map_kiev = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(kiev_center).add_to(map_kiev)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_kiev)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_kiev) 
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Let's zoom in on candidate areas in **Pechersk**:

In [59]:
map_kiev = folium.Map(location=kiev_center, zoom_start=15)
folium.Marker(kiev_center).add_to(map_kiev)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_kiev) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_kiev)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kiev)
folium.GeoJson(kiev_boroughs, style_function=boroughs_style, name='geojson').add_to(map_kiev)
map_kiev

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [60]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = geolocator.geocode([lat, lon]).address.replace(', Україна', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, kiev_center_x, kiev_center_y)
    print('{}{} => {:.1f}km from Khreshchatyk'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Набережне шосе, Царське Село, Видубичі, Печерський район, Київ, 01010 => 2.5km from Khreshchatyk
1/22, Академіка Філатова вулиця, Черепанова гора, Чорна гора, Печерський район, Київ, 01042 => 3.3km from Khreshchatyk
Паркова Дорога вулиця, Дніпровський район, Київ, 01008 => 1.4km from Khreshchatyk
11, Бастіонна вулиця, Бусова гора, Звіринець, Печерський район, Київ, 01014 => 3.9km from Khreshchatyk
Набережне шосе, Царське Село, Видубичі, Печерський район, Київ, 01010 => 3.2km from Khreshchatyk
ДЮСШ з академічного веслування та веслування на байдарках і каное «Київ», Паркова Дорога вулиця, Дніпровський район, Київ, 01008 => 2.2km from Khreshchatyk
12, Лабораторний провулок, Черепанова гора, Печерськ, Печерський район, Київ, 01901 => 2.4km from Khreshchatyk
Набережне шосе, Печерськ, Печерський район, Київ, 01008 => 1.9km from Khreshchatyk
50, Мічуріна вулиця, Царське Село, Звіринець, Печерський район, Київ, 01014 => 3.7km fro

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of cafes and no Coffee places nearby, all zones being fairly close to city center (all less than 4km from Khreshchatyk, and about half of those less than 2km from Khreshchatyk). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential cafe locations. Most of the zones are located in Pechersk boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [62]:
map_kiev = folium.Map(location=roi_center, zoom_start=13)
folium.Circle(kiev_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_kiev)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_kiev) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_kiev)
map_kiev

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of cafes in Kiev (~2000 in our initial area of interest which was 12x12km around Khreshchatyk), there are pockets of low cafe density fairly close to city center. Highest concentration of cafe was detected south and east from Khreshchatyk so we focused our attention to  south, south-east and east from KIev center, corresponding to the borough Pechersk. Our attention was focused on Pechersk which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low cafe density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from Khreshchatyk) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two cafes in radius of 250m and those with an Coffee place closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 8 (we created 15 but 7 of them are located in the Dnieper river so we can't consider them) zones containing largest number of potential new cafe locations based on number of and distance to existing venues - both cafes in general and Coffee places particularly. This, of course, does not imply that those zones are actually optimal locations for a new cafe! Purpose of this analysis was to only provide info on areas close to Kiev center but not crowded with existing cafes (particularly Coffee places) - it is entirely possible that there is a very good reason for small number of cafes in any of those areas, reasons which would make them unsuitable for a new cafe regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify KIev areas close to center with low number of cafes (particularly Coffee places) in order to aid stakeholders in narrowing down the search for optimal location for a new Cafe. By calculating cafe density distribution from Foursquare data we have first identified general borough that justify further analysis (Pechersk), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby cafes. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal cafe location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.